In [3]:
import random
import sqlite3

def do_query(path, q, args=None, commit=False):
    """
    do_query - Run a SQLite query, waiting for DB in necessary

    Args:
        path (str): path to DB file
        q (str): SQL query
        args (list): values for `?` placeholders in q
        commit (bool): whether or not to commit after running query
    Returns:
        list of lists: fetchall() for the query
    """
    if args is None:
        args = []
    for attempt in range(50):
        try:
            con = sqlite3.connect(path)
            cur = con.cursor()
            cur.execute(q, args)
            ans = cur.fetchall()
            if commit:
                con.commit()
            cur.close()
            con.close()
            del cur
            del con
            return ans
        except sqlite3.OperationalError:
            time.sleep(random.randint(10, 30))

In [ ]:
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
from telethon.tl.functions.channels import InviteToChannelRequest
import sys
import csv
import traceback
import time
import asyncio
import warnings
import random

warnings.filterwarnings("ignore")

class TelegramBot:
    def __init__(self, api_id, api_hash, phone):
        
        self.api_id = api_id
        self.api_hash = api_hash
        self.phone = phone
    
    async def startClient(self):
        
        self.client = TelegramClient(self.phone, self.api_id, self.api_hash)
        await self.client.connect()
        
        if not await self.client.is_user_authorized():
            await self.client.send_code_request(self.phone)
            await self.client.sign_in(self.phone,  input('Enter the code: '))
        
    async def getUsersList(self):
        groups = await self.getChannelsList()
        all_members = []
        for i in range(len(groups)):
            target_group=groups[i]
            target_group_entity = InputPeerChannel(target_group.id,target_group.access_hash)    
            print('Fetching Members...' + str(target_group.id))
            #print(all_members)
            all_participants = []
            try:
                all_participants = await self.client.get_participants(target_group, aggressive=True)
            except:
                continue
            #all_members.append(all_participants)
            
            for user in all_participants:
                    if user.username:
                        username= user.username
                    else:
                        username= ""
                    if user.first_name:
                        first_name= user.first_name
                    else:
                        first_name= ""
                    if user.last_name:
                        last_name= user.last_name
                    else:
                        last_name= ""
                    name= (first_name + ' ' + last_name).strip()
                    all_members.append([username,user.id,user.access_hash,name,target_group.title, target_group.id])      
            
        print('Saving In file...')
        #print(all_members)
        
        with open("members.csv","w+",encoding='UTF-8') as f:
                writer = csv.writer(f,delimiter=",",lineterminator="\n")
                csv_dict = [row for row in csv.DictReader(f)]
                if len(csv_dict) == 0:
                    writer.writerow(['username','user id', 'access hash','name','group', 'group id'])
                for user in all_members:
                    writer.writerow(user)      
        
        print('Members saved successfully.')
        
        return all_members
     
    async def getChannelsList(self):
        chats = []
        last_date = None
        chunk_size = 200
        groups=[]
         
        result = await self.client(GetDialogsRequest(
                     offset_date=last_date,
                     offset_id=0,
                     offset_peer=InputPeerEmpty(),
                     limit=chunk_size,
                     hash = 0
                 ))
        chats.extend(result.chats)
        
        for chat in chats:
                try:
                    if chat.megagroup== True:
                        groups.append(chat)
                except:
                    continue
        
        input_file = 'groups.csv'
        with open(input_file,'w+',encoding='UTF-8') as f:
            writer = csv.writer(f,delimiter=",",lineterminator="\n")
            csv_dict = [row for row in csv.DictReader(f)]
            if len(csv_dict) == 0:
                writer.writerow(['group name','group id', 'access hash'])
            for group in groups:
                if group.title:
                    groupname = group.title
                else:
                    groupname = ""
                if group.id:
                    group_id = group.id
                else:
                    group_id = ""
                if group.access_hash:
                    access_hash = group.access_hash
                else:
                    access_hash = ""
                writer.writerow([groupname,group_id,access_hash])   
   
        return groups
        
    async def addMembers(self,group_id, group_access_hash):
        
        #users = self.getUsersList()

        users = []
        
        input_file = 'members.csv'
        with open(input_file, 'r+', encoding='UTF-8') as f:
            rows = csv.reader(f,delimiter=",",lineterminator="\n")
            next(rows, None)
            for row in rows:
                user = {}
                user['username'] = row[0]
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
                user['name'] = row[3]
                users.append(user)
        
        target_group_entity = InputPeerChannel(group_id,group_access_hash)
        
        print(users)
        n = 0
        for user in users:
            n += 1
            if n % 50 == 0:
                time.sleep(900)
            try:
                print ("Adding {}".format(user['id']))
                if user['username'] == "":
                        continue
                user_to_add = self.client.get_input_entity(user['username'])
                self.client(InviteToChannelRequest(target_group_entity,[user_to_add]))
                print("Waiting for 60-180 Seconds...")
                time.sleep(random.randrange(60, 180))
            except PeerFloodError:
                print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
            except UserPrivacyRestrictedError:
                print("The user's privacy settings do not allow you to do this. Skipping.")
            except:
                traceback.print_exc()
                print("Unexpected Error")
                continue

# Access variables Definition
api_id = 2420653
api_hash = 'cf6d7d2c4b0c95e7ffe555079871e579'
phone = '+918124992738'

# Group id
group_id = 1369115731
group_access_hash = '-4683049040197455615'

# Function Calls
telegrambot = TelegramBot(api_id, api_hash, phone)
await telegrambot.startClient()
await telegrambot.getChannelsList()
await telegrambot.getUsersList()
await telegrambot.addMembers(group_id, group_access_hash)


In [ ]:
#users = self.getUsersList()

users = []

input_file = 'members.csv'
with open(input_file, 'w+', encoding='UTF-8') as f:
            rows = csv.reader(f,delimiter=",",lineterminator="\n")
            next(rows, None)
            for row in rows:
                user = {}
                user['username'] = row[0]
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
                user['name'] = row[3]
                users.append(user)
        
target_group_entity = InputPeerChannel(group_id,group_access_hash)
             
for user in users:
            n += 1
            if n % 50 == 0:
                sleep(900)
            try:
                print ("Adding {}".format(user['id']))
                if user['username'] == "":
                        continue
                user_to_add = self.client.get_input_entity(user['username'])
                self.client(InviteToChannelRequest(target_group_entity,[user_to_add]))
                print("Waiting for 60-180 Seconds...")
                time.sleep(random.randrange(60, 180))
            except PeerFloodError:
                print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
            except UserPrivacyRestrictedError:
                print("The user's privacy settings do not allow you to do this. Skipping.")
            except:
                traceback.print_exc()
                print("Unexpected Error")
                continue


In [ ]:
import random
import sqlite3
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
from telethon.tl.functions.channels import InviteToChannelRequest
import sys
import csv
import traceback
import time
import asyncio
import warnings

def do_query(path, q, args=None, commit=False):
    """
    do_query - Run a SQLite query, waiting for DB in necessary

    Args:
        path (str): path to DB file
        q (str): SQL query
        args (list): values for `?` placeholders in q
        commit (bool): whether or not to commit after running query
    Returns:
        list of lists: fetchall() for the query
    """
    if args is None:
        args = []
    for attempt in range(50):
        try:
            con = sqlite3.connect(path)
            cur = con.cursor()
            cur.execute(q, args)
            ans = cur.fetchall()
            if commit:
                con.commit()
            cur.close()
            con.close()
            del cur
            del con
            return ans
        except sqlite3.OperationalError:
            time.sleep(random.randint(10, 30))
            

warnings.filterwarnings("ignore")

class TelegramBot:
    def __init__(self, api_id, api_hash, phone):
        
        self.api_id = api_id
        self.api_hash = api_hash
        self.phone = phone
    
    async def startClient(self):
        
        self.client = TelegramClient(self.phone, self.api_id, self.api_hash)
        await self.client.connect()
        
        if not await self.client.is_user_authorized():
            await self.client.send_code_request(self.phone)
            await self.client.sign_in(self.phone,  input('Enter the code: '))
        
    async def getUsersList(self):
        groups = await self.getChannelsList()
        all_members = []
        for i in range(len(groups)):
            target_group=groups[i]
            target_group_entity = InputPeerChannel(target_group.id,target_group.access_hash)    
            print('Fetching Members...' + str(target_group.id))
            #print(all_members)
            all_participants = []
            try:
                all_participants = await self.client.get_participants(target_group, aggressive=True)
            except:
                continue
            #all_members.append(all_participants)
            
            for user in all_participants:
                    if user.username:
                        username= user.username
                    else:
                        username= ""
                    if user.first_name:
                        first_name= user.first_name
                    else:
                        first_name= ""
                    if user.last_name:
                        last_name= user.last_name
                    else:
                        last_name= ""
                    name= (first_name + ' ' + last_name).strip()
                    all_members.append([username,user.id,user.access_hash,name,target_group.title, target_group.id])      
            
        print('Saving In file...')
        #print(all_members)
        
        with open("members.csv","w+",encoding='UTF-8') as f:
                writer = csv.writer(f,delimiter=",",lineterminator="\n")
                csv_dict = [row for row in csv.DictReader(f)]
                if len(csv_dict) == 0:
                    writer.writerow(['username','user id', 'access hash','name','group', 'group id'])
                for user in all_members:
                    writer.writerow(user)      
        
        print('Members saved successfully.')
        
        return all_members
     
    async def getChannelsList(self):
        chats = []
        last_date = None
        chunk_size = 200
        groups=[]
         
        result = await self.client(GetDialogsRequest(
                     offset_date=last_date,
                     offset_id=0,
                     offset_peer=InputPeerEmpty(),
                     limit=chunk_size,
                     hash = 0
                 ))
        chats.extend(result.chats)
        
        for chat in chats:
                try:
                    if chat.megagroup== True:
                        groups.append(chat)
                except:
                    continue
        
        input_file = 'groups.csv'
        with open(input_file,'w+',encoding='UTF-8') as f:
            writer = csv.writer(f,delimiter=",",lineterminator="\n")
            csv_dict = [row for row in csv.DictReader(f)]
            if len(csv_dict) == 0:
                writer.writerow(['group name','group id', 'access hash'])
            for group in groups:
                if group.title:
                    groupname = group.title
                else:
                    groupname = ""
                if group.id:
                    group_id = group.id
                else:
                    group_id = ""
                if group.access_hash:
                    access_hash = group.access_hash
                else:
                    access_hash = ""
                writer.writerow([groupname,group_id,access_hash])   
   
        return groups
        
    async def addMembers(self,group_id, group_access_hash):
        
        #users = self.getUsersList()

        users = []
        
        input_file = 'members.csv'
        with open(input_file, 'r+', encoding='UTF-8') as f:
            rows = csv.reader(f,delimiter=",",lineterminator="\n")
            next(rows, None)
            for row in rows:
                user = {}
                user['username'] = row[0]
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
                user['name'] = row[3]
                users.append(user)
        
        target_group_entity = InputPeerChannel(group_id,group_access_hash)
        
        print(users)
        n = 0
        for user in users:
            n += 1
            if n % 50 == 0:
                time.sleep(900)
            try:
                print ("Adding {}".format(user['id']))
                if user['username'] == "":
                        continue
                user_to_add = self.client.get_input_entity(user['username'])
                self.client(InviteToChannelRequest(target_group_entity,[user_to_add]))
                print("Waiting for 60-180 Seconds...")
                time.sleep(random.randrange(60, 180))
            except PeerFloodError:
                print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
            except UserPrivacyRestrictedError:
                print("The user's privacy settings do not allow you to do this. Skipping.")
            except:
                traceback.print_exc()
                print("Unexpected Error")
                continue

# Access variables Definition
api_id = API_ID
api_hash = 'API_HASH'
phone = 'Phone_number_with_country_code_with_a_plus' #Eg +919876543210 for Indian number

# Group id
group_id = GROUP_ID 
group_access_hash = 'GROUP_HASH'

# Function Calls
telegrambot = TelegramBot(api_id, api_hash, phone)
await telegrambot.startClient()
await telegrambot.getChannelsList()
await telegrambot.getUsersList()
await telegrambot.addMembers(group_id, group_access_hash)


In [4]:
# Setup.py

from typing import Awaitable
import random
import sqlite3
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
from telethon.tl.functions.channels import InviteToChannelRequest
import sys
import csv
import traceback
import time
import asyncio
import warnings
import nest_asyncio

nest_asyncio.apply()

def do_query(path, q, args=None, commit=False):
    """
    do_query - Run a SQLite query, waiting for DB in necessary

    Args:
        path (str): path to DB file
        q (str): SQL query
        args (list): values for `?` placeholders in q
        commit (bool): whether or not to commit after running query
    Returns:
        list of lists: fetchall() for the query
    """
    if args is None:
        args = []
    for attempt in range(50):
        try:
            con = sqlite3.connect(path)
            cur = con.cursor()
            cur.execute(q, args)
            ans = cur.fetchall()
            if commit:
                con.commit()
            cur.close()
            con.close()
            del cur
            del con
            return ans
        except sqlite3.OperationalError:
            time.sleep(random.randint(10, 30))
            

warnings.filterwarnings("ignore")

class TelegramBot:
    def __init__(self, api_id, api_hash, phone):
        
        self.api_id = api_id
        self.api_hash = api_hash
        self.phone = phone
    
    async def startClient(self):
        
        self.client = TelegramClient(self.phone, self.api_id, self.api_hash)
        await self.client.connect()
        
        if not await self.client.is_user_authorized():
            await self.client.send_code_request(self.phone)
            await self.client.sign_in(self.phone,  input('Enter the code: '))
        
    async def getUsersList(self):
        groups = await self.getChannelsList()
        all_members = []
        for i in range(len(groups)):
            target_group=groups[i]
            target_group_entity = InputPeerChannel(target_group.id,target_group.access_hash)    
            print('Fetching Members...' + str(target_group.id))
            #print(all_members)
            all_participants = []
            try:
                all_participants = await self.client.get_participants(target_group, aggressive=True)
            except:
                continue
            #all_members.append(all_participants)
            
            for user in all_participants:
                    if user.username:
                        username= user.username
                    else:
                        username= ""
                    if user.first_name:
                        first_name= user.first_name
                    else:
                        first_name= ""
                    if user.last_name:
                        last_name= user.last_name
                    else:
                        last_name= ""
                    name= (first_name + ' ' + last_name).strip()
                    all_members.append([username,user.id,user.access_hash,name,target_group.title, target_group.id])      
            
        print('Saving In file...')
        #print(all_members)
        
        with open("members.csv","w+",encoding='UTF-8') as f:
                writer = csv.writer(f,delimiter=",",lineterminator="\n")
                csv_dict = [row for row in csv.DictReader(f)]
                if len(csv_dict) == 0:
                    writer.writerow(['username','user id', 'access hash','name','group', 'group id'])
                for user in all_members:
                    writer.writerow(user)      
        
        print('Members saved successfully.')
        
        return all_members
     
    async def getChannelsList(self):
        chats = []
        last_date = None
        chunk_size = 200
        groups=[]
         
        result = await self.client(GetDialogsRequest(
                     offset_date=last_date,
                     offset_id=0,
                     offset_peer=InputPeerEmpty(),
                     limit=chunk_size,
                     hash = 0
                 ))
        chats.extend(result.chats)
        
        for chat in chats:
                try:
                    if chat.megagroup== True:
                        groups.append(chat)
                except:
                    continue
        
        input_file = 'groups.csv'
        with open(input_file,'w+',encoding='UTF-8') as f:
            writer = csv.writer(f,delimiter=",",lineterminator="\n")
            csv_dict = [row for row in csv.DictReader(f)]
            if len(csv_dict) == 0:
                writer.writerow(['group name','group id', 'access hash'])
            for group in groups:
                if group.title:
                    groupname = group.title
                else:
                    groupname = ""
                if group.id:
                    group_id = group.id
                else:
                    group_id = ""
                if group.access_hash:
                    access_hash = group.access_hash
                else:
                    access_hash = ""
                writer.writerow([groupname,group_id,access_hash])   
   
        return groups
        
    async def addMembers(self,group_id, group_access_hash):
        
        #users = self.getUsersList()

        users = []
        
        input_file = 'members.csv'
        with open(input_file, 'r+', encoding='UTF-8') as f:
            rows = csv.reader(f,delimiter=",",lineterminator="\n")
            next(rows, None)
            for row in rows:
                user = {}
                user['username'] = row[0]
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
                user['name'] = row[3]
                users.append(user)
        
        target_group_entity = InputPeerChannel(group_id,group_access_hash)
        
        print(users)
        n = 0
        for user in users:
            n += 1
            if n % 50 == 0:
                time.sleep(900)
            try:
                print ("Adding {}".format(user['id']))
                if user['username'] == "":
                        continue
                user_to_add = self.client.get_input_entity(user['username'])
                self.client(InviteToChannelRequest(target_group_entity,[user_to_add]))
                print("Waiting for 60-180 Seconds...")
                time.sleep(random.randrange(60, 180))
            except PeerFloodError:
                print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
            except UserPrivacyRestrictedError:
                print("The user's privacy settings do not allow you to do this. Skipping.")
            except:
                traceback.print_exc()
                print("Unexpected Error")
                continue
                
async def telebot():
    # Access variables Definition
    api_id = API_ID
    api_hash = 'API_HASH'
    phone = 'Phone_number_with_country_code_with_a_plus' #Eg +919876543210 for Indian number

    # Group id
    #group_id = GROUP_ID 
    #group_access_hash = 'GROUP_HASH'

    # Function Calls
    telegrambot = TelegramBot(api_id, api_hash, phone)
    await telegrambot.startClient()
    await telegrambot.getChannelsList()
    #await telegrambot.getUsersList()
    #await telegrambot.addMembers(group_id, group_access_hash)

loop = asyncio.get_event_loop()
loop.run_until_complete(telebot())

<coroutine object telebot at 0x7f4fc449dbc0>

In [3]:
# telebot.py

from typing import Awaitable
import random
import sqlite3
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
from telethon.tl.functions.channels import InviteToChannelRequest
import sys
import csv
import traceback
import time
import asyncio
import warnings
import nest_asyncio

nest_asyncio.apply()

def do_query(path, q, args=None, commit=False):
    """
    do_query - Run a SQLite query, waiting for DB in necessary

    Args:
        path (str): path to DB file
        q (str): SQL query
        args (list): values for `?` placeholders in q
        commit (bool): whether or not to commit after running query
    Returns:
        list of lists: fetchall() for the query
    """
    if args is None:
        args = []
    for attempt in range(50):
        try:
            con = sqlite3.connect(path)
            cur = con.cursor()
            cur.execute(q, args)
            ans = cur.fetchall()
            if commit:
                con.commit()
            cur.close()
            con.close()
            del cur
            del con
            return ans
        except sqlite3.OperationalError:
            time.sleep(random.randint(10, 30))
            

warnings.filterwarnings("ignore")

class TelegramBot:
    def __init__(self, api_id, api_hash, phone):
        
        self.api_id = api_id
        self.api_hash = api_hash
        self.phone = phone
    
    async def startClient(self):
        
        self.client = TelegramClient(self.phone, self.api_id, self.api_hash)
        await self.client.connect()
        
        if not await self.client.is_user_authorized():
            await self.client.send_code_request(self.phone)
            await self.client.sign_in(self.phone,  input('Enter the code: '))
        
    async def getUsersList(self, target_group_id, target_group_access_hash):
        all_members = []
        target_group_entity = InputPeerChannel(target_group_id,target_group_access_hash)    
        print('Fetching Members...' + str(target_group_id))
        #print(all_members)
        all_participants = []
        while True:
            try:
                all_participants = await self.client.get_participants(target_group_id, aggressive=True)
            except:
                continue
        #all_members.append(all_participants)
            
        for user in all_participants:
                    if user.username:
                        username= user.username
                    else:
                        username= ""
                    if user.first_name:
                        first_name= user.first_name
                    else:
                        first_name= ""
                    if user.last_name:
                        last_name= user.last_name
                    else:
                        last_name= ""
                    name= (first_name + ' ' + last_name).strip()
                    all_members.append([username,user.id,user.access_hash,name,target_group.title, target_group.id])      
            
        print('Saving In file...')
        #print(all_members)
        
        with open("members.csv","w+",encoding='UTF-8') as f:
                writer = csv.writer(f,delimiter=",",lineterminator="\n")
                csv_dict = [row for row in csv.DictReader(f)]
                if len(csv_dict) == 0:
                    writer.writerow(['username','user id', 'access hash','name','group', 'group id'])
                for user in all_members:
                    writer.writerow(user)      
        
        print('Members saved successfully.')
        
        return all_members
     
    
    async def addMembers(self,group_id, group_access_hash):
        
        #users = self.getUsersList()

        users = []
        
        input_file = 'members.csv'
        with open(input_file, 'r+', encoding='UTF-8') as f:
            rows = csv.reader(f,delimiter=",",lineterminator="\n")
            next(rows, None)
            for row in rows:
                user = {}
                user['username'] = row[0]
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
                user['name'] = row[3]
                users.append(user)
        
        target_group_entity = InputPeerChannel(group_id,group_access_hash)
        
        print(users)
        n = 0
        for user in users:
            n += 1
            if n % 50 == 0:
                time.sleep(900)
            try:
                print ("Adding {}".format(user['id']))
                if user['username'] == "":
                        continue
                user_to_add = self.client.get_input_entity(user['username'])
                self.client(InviteToChannelRequest(target_group_entity,[user_to_add]))
                print("Waiting for 60-180 Seconds...")
                time.sleep(random.randrange(60, 180))
            except PeerFloodError:
                print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
            except UserPrivacyRestrictedError:
                print("The user's privacy settings do not allow you to do this. Skipping.")
            except:
                traceback.print_exc()
                print("Unexpected Error")
                continue
                
async def telebot():
    # Access variables Definition
    api_id = API_ID
    api_hash = 'API_HASH'
    phone = 'Phone_number_with_country_code_with_a_plus' #Eg +919876543210 for Indian number

    # Group id
    #group_id = GROUP_ID 
    #group_access_hash = 'GROUP_HASH'
    
    # Target group from which you want the members
    target_group_id = TARGET_GROUP_ID #Target group id
    target_group_access_hash = 'TARGET_GROUP_ACCESS_HASH'

    # Function Calls
    telegrambot = TelegramBot(api_id, api_hash, phone)
    await telegrambot.startClient()
    #await telegrambot.getChannelsList()
    await telegrambot.getUsersList(target_group_id,target_group_access_hash)
    await telegrambot.addMembers(group_id, group_access_hash)

loop = asyncio.get_event_loop()
loop.run_until_complete(telebot())

NameError: name 'API_ID' is not defined

In [ ]:
# Setup.py

#from typing import Awaitable
import random
import sqlite3
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
from telethon.tl.functions.channels import InviteToChannelRequest
import sys
import csv
import traceback
import time
import asyncio
import warnings
import nest_asyncio

nest_asyncio.apply()

def do_query(path, q, args=None, commit=False):
    """
    do_query - Run a SQLite query, waiting for DB in necessary

    Args:
        path (str): path to DB file
        q (str): SQL query
        args (list): values for `?` placeholders in q
        commit (bool): whether or not to commit after running query
    Returns:
        list of lists: fetchall() for the query
    """
    if args is None:
        args = []
    for attempt in range(50):
        try:
            con = sqlite3.connect(path)
            cur = con.cursor()
            cur.execute(q, args)
            ans = cur.fetchall()
            if commit:
                con.commit()
            cur.close()
            con.close()
            del cur
            del con
            return ans
        except sqlite3.OperationalError:
            time.sleep(random.randint(10, 30))
            

warnings.filterwarnings("ignore")

class TelegramBot:
    def __init__(self, api_id, api_hash, phone):
        
        self.api_id = api_id
        self.api_hash = api_hash
        self.phone = phone
    
    async def startClient(self):
        
        self.client = TelegramClient(self.phone, self.api_id, self.api_hash)
        await self.client.connect()
        
        if not await self.client.is_user_authorized():
            await self.client.send_code_request(self.phone)
            await self.client.sign_in(self.phone,  input('Enter the code: '))
        
    async def getUsersList(self):
        groups = await self.getChannelsList()
        all_members = []
        for i in range(len(groups)):
            target_group=groups[i]
            target_group_entity = InputPeerChannel(target_group.id,target_group.access_hash)    
            print('Fetching Members...' + str(target_group.id))
            #print(all_members)
            all_participants = []
            try:
                all_participants = await self.client.get_participants(target_group, aggressive=True)
            except:
                continue
            #all_members.append(all_participants)
            
            for user in all_participants:
                    if user.username:
                        username= user.username
                    else:
                        username= ""
                    if user.first_name:
                        first_name= user.first_name
                    else:
                        first_name= ""
                    if user.last_name:
                        last_name= user.last_name
                    else:
                        last_name= ""
                    name= (first_name + ' ' + last_name).strip()
                    all_members.append([username,user.id,user.access_hash,name,target_group.title, target_group.id])      
            
        print('Saving In file...')
        #print(all_members)
        
        with open("members.csv","w+",encoding='UTF-8') as f:
                writer = csv.writer(f,delimiter=",",lineterminator="\n")
                csv_dict = [row for row in csv.DictReader(f)]
                if len(csv_dict) == 0:
                    writer.writerow(['username','user id', 'access hash','name','group', 'group id'])
                for user in all_members:
                    writer.writerow(user)      
        
        print('Members saved successfully.')
        
        return all_members
     
    async def getChannelsList(self):
        chats = []
        last_date = None
        chunk_size = 200
        groups=[]
         
        result = await self.client(GetDialogsRequest(
                     offset_date=last_date,
                     offset_id=0,
                     offset_peer=InputPeerEmpty(),
                     limit=chunk_size,
                     hash = 0
                 ))
        chats.extend(result.chats)
        
        for chat in chats:
                try:
                    if chat.megagroup== True:
                        groups.append(chat)
                except:
                    continue
        
        input_file = 'groups.csv'
        with open(input_file,'w+',encoding='UTF-8') as f:
            writer = csv.writer(f,delimiter=",",lineterminator="\n")
            csv_dict = [row for row in csv.DictReader(f)]
            if len(csv_dict) == 0:
                writer.writerow(['group name','group id', 'access hash'])
            for group in groups:
                if group.title:
                    groupname = group.title
                else:
                    groupname = ""
                if group.id:
                    group_id = group.id
                else:
                    group_id = ""
                if group.access_hash:
                    access_hash = group.access_hash
                else:
                    access_hash = ""
                writer.writerow([groupname,group_id,access_hash])   
   
        return groups
        
    async def addMembers(self,group_id, group_access_hash):
        
        #users = self.getUsersList()

        users = []
        
        input_file = 'members2.csv'
        with open(input_file, 'r+', encoding='UTF-8') as f:
            rows = csv.reader(f,delimiter=",",lineterminator="\n")
            next(rows, None)
            for row in rows:
                user = {}
                user['username'] = row[0]
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
                user['name'] = row[3]
                users.append(user)
        
        target_group_entity = InputPeerChannel(group_id,group_access_hash)
        
        print(users)
        n = 0
        for user in users:
            n += 1
            if n % 50 == 0:
                time.sleep(900)
            try:
                print ("Adding {}".format(user['id']))
                if user['username'] == "":
                        continue
                user_to_add = self.client.get_input_entity(user['username'])
                self.client(InviteToChannelRequest(target_group_entity,[user_to_add]))
                print("Waiting for 60-180 Seconds...")
                time.sleep(random.randrange(60, 180))
            except PeerFloodError:
                print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
            except UserPrivacyRestrictedError:
                print("The user's privacy settings do not allow you to do this. Skipping.")
            except:
                traceback.print_exc()
                print("Unexpected Error")
                continue
                
async def telebot():
    # Access variables Definition
    api_id = 2420653
    api_hash = 'cf6d7d2c4b0c95e7ffe555079871e579'
    phone = '+918124992738'

    # Group id
    #group_id = GROUP_ID 
    #group_access_hash = 'GROUP_HASH'

    # Function Calls
    telegrambot = TelegramBot(api_id, api_hash, phone)
    await telegrambot.startClient()
    await telegrambot.getChannelsList()
    #await telegrambot.getUsersList()
    #await telegrambot.addMembers(group_id, group_access_hash)

loop = asyncio.get_event_loop()
loop.run_until_complete(telebot())
#loop.close()

In [4]:
pip install nest_asyncio

Note: you may need to restart the kernel to use updated packages.


In [ ]:
# Setup.py

#from typing import Awaitable
import random
import sqlite3
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
from telethon.tl.functions.channels import InviteToChannelRequest
import sys
import csv
import traceback
import time
import asyncio
import warnings
import nest_asyncio

nest_asyncio.apply()

def do_query(path, q, args=None, commit=False):
    """
    do_query - Run a SQLite query, waiting for DB in necessary

    Args:
        path (str): path to DB file
        q (str): SQL query
        args (list): values for `?` placeholders in q
        commit (bool): whether or not to commit after running query
    Returns:
        list of lists: fetchall() for the query
    """
    if args is None:
        args = []
    for attempt in range(50):
        try:
            con = sqlite3.connect(path)
            cur = con.cursor()
            cur.execute(q, args)
            ans = cur.fetchall()
            if commit:
                con.commit()
            cur.close()
            con.close()
            del cur
            del con
            return ans
        except sqlite3.OperationalError:
            time.sleep(random.randint(10, 30))
            

warnings.filterwarnings("ignore")

class TelegramBot:
    def __init__(self, api_id, api_hash, phone):
        
        self.api_id = api_id
        self.api_hash = api_hash
        self.phone = phone
    
    async def startClient(self):
        
        self.client = TelegramClient(self.phone, self.api_id, self.api_hash)
        await self.client.connect()
        
        if not await self.client.is_user_authorized():
            await self.client.send_code_request(self.phone)
            await self.client.sign_in(self.phone,  input('Enter the code: '))
        
    async def getUsersList(self):
        groups = await self.getChannelsList()
        all_members = []
        for i in range(len(groups)):
            target_group=groups[i]
            target_group_entity = InputPeerChannel(target_group.id,target_group.access_hash)    
            print('Fetching Members...' + str(target_group.id))
            #print(all_members)
            all_participants = []
            try:
                all_participants = await self.client.get_participants(target_group, aggressive=True)
            except:
                continue
            #all_members.append(all_participants)
            
            for user in all_participants:
                    if user.username:
                        username= user.username
                    else:
                        username= ""
                    if user.first_name:
                        first_name= user.first_name
                    else:
                        first_name= ""
                    if user.last_name:
                        last_name= user.last_name
                    else:
                        last_name= ""
                    name= (first_name + ' ' + last_name).strip()
                    all_members.append([username,user.id,user.access_hash,name,target_group.title, target_group.id])      
            
        print('Saving In file...')
        #print(all_members)
        
        with open("members.csv","w+",encoding='UTF-8') as f:
                writer = csv.writer(f,delimiter=",",lineterminator="\n")
                csv_dict = [row for row in csv.DictReader(f)]
                if len(csv_dict) == 0:
                    writer.writerow(['username','user id', 'access hash','name','group', 'group id'])
                for user in all_members:
                    writer.writerow(user)      
        
        print('Members saved successfully.')
        
        return all_members
     
    async def getChannelsList(self):
        chats = []
        last_date = None
        chunk_size = 200
        groups=[]
         
        result = await self.client(GetDialogsRequest(
                     offset_date=last_date,
                     offset_id=0,
                     offset_peer=InputPeerEmpty(),
                     limit=chunk_size,
                     hash = 0
                 ))
        chats.extend(result.chats)
        
        for chat in chats:
                try:
                    if chat.megagroup== True:
                        groups.append(chat)
                except:
                    continue
        
        input_file = 'groups.csv'
        with open(input_file,'w+',encoding='UTF-8') as f:
            writer = csv.writer(f,delimiter=",",lineterminator="\n")
            csv_dict = [row for row in csv.DictReader(f)]
            if len(csv_dict) == 0:
                writer.writerow(['group name','group id', 'access hash'])
            for group in groups:
                if group.title:
                    groupname = group.title
                else:
                    groupname = ""
                if group.id:
                    group_id = group.id
                else:
                    group_id = ""
                if group.access_hash:
                    access_hash = group.access_hash
                else:
                    access_hash = ""
                writer.writerow([groupname,group_id,access_hash])   
   
        return groups
        
    async def addMembers(self,group_id, group_access_hash):
        
        #users = self.getUsersList()

        users = []
        
        input_file = 'members2.csv'
        with open(input_file, 'r+', encoding='UTF-8') as f:
            rows = csv.reader(f,delimiter=",",lineterminator="\n")
            next(rows, None)
            for row in rows:
                user = {}
                user['username'] = row[0]
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
                user['name'] = row[3]
                users.append(user)
        
        target_group_entity = InputPeerChannel(group_id,group_access_hash)
        
        print(users)
        n = 0
        for user in users:
            n += 1
            if n % 50 == 0:
                time.sleep(900)
            try:
                print ("Adding {}".format(user['id']))
                if user['username'] == "":
                        continue
                user_to_add = self.client.get_input_entity(user['username'])
                self.client(InviteToChannelRequest(target_group_entity,[user_to_add]))
                print("Waiting for 60-180 Seconds...")
                time.sleep(random.randrange(60, 180))
            except PeerFloodError:
                print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
            except UserPrivacyRestrictedError:
                print("The user's privacy settings do not allow you to do this. Skipping.")
            except:
                traceback.print_exc()
                print("Unexpected Error")
                continue
                
async def telebot():
    # Access variables Definition
    api_id = 2420653
    api_hash = 'cf6d7d2c4b0c95e7ffe555079871e579'
    phone = '+918124992738'

    # Group id
    group_id = 1369115731
    group_access_hash = '-4683049040197455615'

    # Function Calls
    telegrambot = TelegramBot(api_id, api_hash, phone)
    await telegrambot.startClient()
    #await telegrambot.getChannelsList()
    #await telegrambot.getUsersList()
    await telegrambot.addMembers(member_id, group_id, group_access_hash)

loop = asyncio.get_event_loop()
loop.run_until_complete(telebot())
#loop.close()

In [ ]:
# Setup.py

#from typing import Awaitable
import random
import sqlite3
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
from telethon.tl.functions.channels import InviteToChannelRequest
import sys
import csv
import traceback
import time
import asyncio
import warnings
import nest_asyncio

nest_asyncio.apply()

def do_query(path, q, args=None, commit=False):
    """
    do_query - Run a SQLite query, waiting for DB in necessary

    Args:
        path (str): path to DB file
        q (str): SQL query
        args (list): values for `?` placeholders in q
        commit (bool): whether or not to commit after running query
    Returns:
        list of lists: fetchall() for the query
    """
    if args is None:
        args = []
    for attempt in range(50):
        try:
            con = sqlite3.connect(path)
            cur = con.cursor()
            cur.execute(q, args)
            ans = cur.fetchall()
            if commit:
                con.commit()
            cur.close()
            con.close()
            del cur
            del con
            return ans
        except sqlite3.OperationalError:
            time.sleep(random.randint(10, 30))
            

warnings.filterwarnings("ignore")

class TelegramBot:
    def __init__(self, api_id, api_hash, phone):
        
        self.api_id = api_id
        self.api_hash = api_hash
        self.phone = phone
    
    async def startClient(self):
        
        self.client = TelegramClient(self.phone, self.api_id, self.api_hash)
        await self.client.connect()
        
        if not await self.client.is_user_authorized():
            await self.client.send_code_request(self.phone)
            await self.client.sign_in(self.phone,  input('Enter the code: '))
        
    async def getUsersList(self):
        all_members = []
        target_group_entity = InputPeerChannel(1369115731,'-4683049040197455615')    
        print('Fetching Members...' + str(1369115731))
        #print(all_members)
        all_participants = []
        while True:
            try:
                all_participants = await self.client.get_participants(target_group_entity, aggressive=True)
            except:
                continue
        #all_members.append(all_participants)
            
        for user in all_participants:
                    if user.username:
                        username= user.username
                    else:
                        username= ""
                    if user.first_name:
                        first_name= user.first_name
                    else:
                        first_name= ""
                    if user.last_name:
                        last_name= user.last_name
                    else:
                        last_name= ""
                    name= (first_name + ' ' + last_name).strip()
                    all_members.append([username,user.id,user.access_hash,name,'Royap Entre.', 1369115731])      
            
        print('Saving In file...')
        #print(all_members)
        
        with open("members_royentr.csv","w+",encoding='UTF-8') as f:
                writer = csv.writer(f,delimiter=",",lineterminator="\n")
                csv_dict = [row for row in csv.DictReader(f)]
                if len(csv_dict) == 0:
                    writer.writerow(['username','user id', 'access hash','name','group', 'group id'])
                for user in all_members:
                    writer.writerow(user)      
        
        print('Members saved successfully.')
        
        return all_members
     
    async def getChannelsList(self):
        chats = []
        last_date = None
        chunk_size = 200
        groups=[]
         
        result = await self.client(GetDialogsRequest(
                     offset_date=last_date,
                     offset_id=0,
                     offset_peer=InputPeerEmpty(),
                     limit=chunk_size,
                     hash = 0
                 ))
        chats.extend(result.chats)
        
        for chat in chats:
                try:
                    if chat.megagroup== True:
                        groups.append(chat)
                except:
                    continue
        
        input_file = 'groups.csv'
        with open(input_file,'w+',encoding='UTF-8') as f:
            writer = csv.writer(f,delimiter=",",lineterminator="\n")
            csv_dict = [row for row in csv.DictReader(f)]
            if len(csv_dict) == 0:
                writer.writerow(['group name','group id', 'access hash'])
            for group in groups:
                if group.title:
                    groupname = group.title
                else:
                    groupname = ""
                if group.id:
                    group_id = group.id
                else:
                    group_id = ""
                if group.access_hash:
                    access_hash = group.access_hash
                else:
                    access_hash = ""
                writer.writerow([groupname,group_id,access_hash])   
   
        return groups
        
    async def addMembers(self,group_id, group_access_hash):
        
        #users = self.getUsersList()

        users = []
        
        input_file = 'members2.csv'
        with open(input_file, 'r+', encoding='UTF-8') as f:
            rows = csv.reader(f,delimiter=",",lineterminator="\n")
            next(rows, None)
            for row in rows:
                user = {}
                user['username'] = row[0]
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
                user['name'] = row[3]
                users.append(user)
        
        target_group_entity = InputPeerChannel(group_id,group_access_hash)
        
        print(users)
        n = 0
        for user in users:
            n += 1
            if n % 50 == 0:
                time.sleep(900)
            try:
                print ("Adding {}".format(user['id']))
                if user['username'] == "":
                        continue
                user_to_add = self.client.get_input_entity(user['username'])
                self.client(InviteToChannelRequest(target_group_entity,[user_to_add]))
                print("Waiting for 60-180 Seconds...")
                time.sleep(random.randrange(60, 180))
            except PeerFloodError:
                print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
            except UserPrivacyRestrictedError:
                print("The user's privacy settings do not allow you to do this. Skipping.")
            except:
                traceback.print_exc()
                print("Unexpected Error")
                continue
                
async def telebot():
    # Access variables Definition
    api_id = 2420653
    api_hash = 'cf6d7d2c4b0c95e7ffe555079871e579'
    phone = '+918124992738'

    # Group id
    #group_id = GROUP_ID 
    #group_access_hash = 'GROUP_HASH'

    # Function Calls
    telegrambot = TelegramBot(api_id, api_hash, phone)
    await telegrambot.startClient()
    #await telegrambot.getChannelsList()
    await telegrambot.getUsersList()
    #await telegrambot.addMembers(group_id, group_access_hash)

loop = asyncio.get_event_loop()
loop.run_until_complete(telebot())
#loop.close()

Fetching Members...1369115731


In [ ]:
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
from telethon.tl.functions.channels import InviteToChannelRequest
from telethon.tl.functions.messages import AddChatUserRequest
import sys
import csv
import traceback
import time
import random
import re
import asyncio


api_id = 2420653        # YOUR API_ID
api_hash = 'cf6d7d2c4b0c95e7ffe555079871e579'        # YOUR API_HASH
phone = '+918124992738'        # YOUR PHONE NUMBER, INCLUDING COUNTRY CODE
client = TelegramClient(phone, api_id, api_hash)

await client.connect()
if not await client.is_user_authorized():
    await client.send_code_request(phone)
    await client.sign_in(phone, input('Enter the code: '))

async def add_users_to_group():
    input_file = 'members.csv'
    users = []
    with open(input_file, encoding='UTF-8') as f:
        rows = csv.reader(f,delimiter=",",lineterminator="\n")
        next(rows, None)
        for row in rows:
            user = {}
            user['username'] = row[0]
            try:
                user['id'] = int(row[1])
                user['access_hash'] = int(row[2])
            except IndexError:
                print ('users without id or access_hash')
            users.append(user)

    #random.shuffle(users)
    chats = []
    last_date = None
    chunk_size = 200
    groups=[]

    result = await client(GetDialogsRequest(
                offset_date=last_date,
                offset_id=0,
                offset_peer=InputPeerEmpty(),
                limit=chunk_size,
                hash = 0
            ))
    chats.extend(result.chats)
    
    
    for chat in chats:
        try:
            if await chat.megagroup== True: # CONDITION TO ONLY LIST MEGA GROUPS.
                groups.append(chat)
        except:
            continue
    
    print(groups)
    
    #print('Choose a group to add members:')
    i=0
    for group in groups:
        print(str(i) + '- ' + group.title)
        i+=1

    g_index = input("Enter a Number: ")
    target_group=groups[int(g_index)]
    print('\n\nGrupo elegido:\t' + groups[int(g_index)].title)

    target_group_entity = await InputPeerChannel(target_group.id,target_group.access_hash)

    mode = int(input("Enter 1 to add by username or 2 to add by ID: "))

    error_count = 0

    for user in users:
        try:
            print ("Adding {}".format(user['username']))
            if mode == 1:
                if user['username'] == "":
                    continue
                user_to_add = await client.get_input_entity(user['username'])
            elif mode == 2:
                user_to_add = InputPeerUser(user['id'], user['access_hash'])
            else:
                sys.exit("Invalid Mode Selected. Please Try Again.")
            await client(InviteToChannelRequest(target_group_entity,[user_to_add]))
            print("Waiting 60 Seconds...")
            time.sleep(60)
        except PeerFloodError:
            print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
        except UserPrivacyRestrictedError:
            print("The user's privacy settings do not allow you to do this. Skipping.")
        except:
            traceback.print_exc()
            print("Unexpected Error")
            error_count += 1
            if error_count > 10:
                sys.exit('too many errors')
            continue

async def list_users_in_group():
    chats = []
    last_date = None
    chunk_size = 200
    groups=[]
    
    result = await client(GetDialogsRequest(
                offset_date=last_date,
                offset_id=0,
                offset_peer=InputPeerEmpty(),
                limit=chunk_size,
                hash = 0
            ))
    chats.extend(result.chats)
    
    for chat in chats:
        try:
            print(chat)
            groups.append(chat)
            # if chat.megagroup== True:
        except:
            continue
    
    print('Choose a group to scrape members from:')
    i=0
    for g in groups:
        print(str(i) + '- ' + g.title)
        i+=1
        
    print(groups)
    
    g_index = input("Enter a Number: ")
    target_group=groups[int(g_index)]

    print('\n\nGrupo elegido:\t' + groups[int(g_index)].title)
    
    print('Fetching Members...')
    all_participants = []
    all_participants = await client.get_participants(target_group, aggressive=True)
    
    print('Saving In file...')
    with open("members-" + re.sub("-+","-",re.sub("[^a-zA-Z]","-",str.lower(target_group.title))) + ".csv","w",encoding='UTF-8') as f:
        writer = csv.writer(f,delimiter=",",lineterminator="\n")
        writer.writerow(['username','user id', 'access hash','name','group', 'group id'])
        for user in all_participants:
            if user.username:
                username= user.username
            else:
                username= ""
            if user.first_name:
                first_name= user.first_name
            else:
                first_name= ""
            if user.last_name:
                last_name= user.last_name
            else:
                last_name= ""
            name= (first_name + ' ' + last_name).strip()
            writer.writerow([username,user.id,user.access_hash,name,target_group.title, target_group.id])      
    print('Members scraped successfully.')

def printCSV():
    input_file = sys.argv[1]
    users = []
    with open(input_file, encoding='UTF-8') as f:
        rows = csv.reader(f,delimiter=",",lineterminator="\n")
        next(rows, None)
        for row in rows:
            user = {}
            user['username'] = row[0]
            user['id'] = int(row[1])
            user['access_hash'] = int(row[2])
            users.append(user)
            print(row)
            print(user)
    sys.exit('FINITO')

# print('Fetching Members...')
# all_participants = []
# all_participants = client.get_participants(target_group, aggressive=True)
print('What do you want to do:')
mode = int(input("Enter \n1-List users in a group\n2-Add users from CSV to Group (CSV must be passed as a parameter to the script\n3-Show CSV\n\nYour option:  "))

if mode == 1:
    await list_users_in_group()
elif mode == 2:
    await add_users_to_group()
elif mode == 3:
    printCSV()


In [ ]:
from telethon.sync import TelegramClient
from telethon.tl.functions.messages import GetDialogsRequest
from telethon.tl.types import InputPeerEmpty, InputPeerChannel, InputPeerUser
from telethon.errors.rpcerrorlist import PeerFloodError, UserPrivacyRestrictedError
#from telethon.tl.functions.channels import InviteToChannelRequest
from telethon.tl.functions.channels import JoinChannelRequest
import sys
import csv
import traceback
import time

api_id = 2420653
api_hash = 'cf6d7d2c4b0c95e7ffe555079871e579'
phone = '+918124992738'
client = TelegramClient(phone, api_id, api_hash)

await client.connect()
if not await client.is_user_authorized():
    await client.send_code_request(phone)
    await client.sign_in(phone, input('Enter the code: '))

"""
input_file = 'members.csv'
users = []
with open(input_file, encoding='UTF-8') as f:
    rows = csv.reader(f,delimiter=",",lineterminator="\n")
    next(rows, None)
    for row in rows:
        user = {}
        user['username'] = row[0]
        user['id'] = int(row[1])
        user['access_hash'] = int(row[2])
        user['name'] = row[3]
        users.append(user)
"""

#users = []
users = [
  {"username": "",
  "id": 1450914405,
  "access_hash": '-7750098715601952191'}]
chats = []
last_date = None
chunk_size = 200
groups=[]

result = await client(GetDialogsRequest(
             offset_date=last_date,
             offset_id=0,
             offset_peer=InputPeerEmpty(),
             limit=chunk_size,
             hash = 0
         ))
chats.extend(result.chats)

for chat in chats:
    try:
        if chat.megagroup== True:
            groups.append(chat)
    except:
        continue

print('Choose a group to add members:')
i=0
for group in groups:
    print(str(i) + '- ' + group.title)
    i+=1

g_index = input("Enter a Number: ")
target_group=groups[int(g_index)]

target_group_entity = InputPeerChannel(target_group.id,target_group.access_hash)

#messages.addChatUser


mode = int(input("Enter 1 to add by username or 2 to add by ID: "))

while True:
    try:
        print ("Adding {}".format(1450914405))
        if mode == 1:
            #if user['username'] == "":
            #    continue
            #user_to_add = client.get_input_entity(user['username'])
            print('None')
        elif mode == 2:
            user_to_add = InputPeerUser(1450914405,'-7750098715601952191')
        else:
            sys.exit("Invalid Mode Selected. Please Try Again.")
        #await client(InviteToChannelRequest(target_group_entity,[user_to_add]))
        await client(JoinChannelRequest(target_group_entity,[user_to_add]))
        print("Waiting 60 Seconds...")
        time.sleep(60)
    except PeerFloodError:
        print("Getting Flood Error from telegram. Script is stopping now. Please try again after some time.")
    except UserPrivacyRestrictedError:
        print("The user's privacy settings do not allow you to do this. Skipping.")
    except:
        traceback.print_exc()
        print("Unexpected Error")
        #print(str(traceback.print_exc()))
        #print(traceback.print_exc())
        continue

Enter the code:  60028


Choose a group to add members:
0- Royapuram Entrepreneurs🤘
1- STARTUP FOUNDERS & Entrepreneurs | Apex Founders
2- StartupLanes.com
3- KaroStartup
4- Entrepreneurial journey (EJ) | Startup Monk
5- African Business Network
6- Freelance Buddy
7- Madhavaram Joly Group
8- GLOBAL CRYPTO INVEST
9- Bot testing
10- BotCapsule [Automate Everything]
11- ❤️Make money every day
12- Legends of Tomorrow🪂🏄‍♂ Chennai Edition
13- Data Chat


Enter a Number:  0
Enter 1 to add by username or 2 to add by ID:  2


Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Un

Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-

...

Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Add

Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-

Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Add

Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-input-1-e37ff8f0f838>", line 92, in <module>
    await client(JoinChannelRequest(target_group_entity,[user_to_add]))
TypeError: __init__() takes 2 positional arguments but 3 were given
Traceback (most recent call last):
  File "<ipython-

Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Adding 1450914405
Unexpected Error
Add